In [1]:
import pandas as pd
import entitymatching as em

/usr/local/lib/python3.5/dist-packages/fuzzywuzzy/fuzz.py:35: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [2]:
from py2neo import Graph, ConstraintError

In [3]:
from datetime import datetime

In [4]:
import numpy as np

In [5]:
core1peopleFileName = 'corepeople1.csv'
dobFileName = 'dob_data_b.csv'

In [7]:
core1people = pd.read_csv(core1peopleFileName)
dobBOD = pd.read_csv(dobFileName)

In [8]:
core1people.head()

din                    name
0  00000001        RATAN NAVAL TATA
1  00000002   RAMADORAI SUBRAMANIAN
2  00001033    RAMANATHAN NARAYANAN
3  00001049          RAJESH CHHARIA
4  00001050  AMIT AMARNATH BHARGAVA

In [9]:
dobBOD.head()

Unnamed: 0   din                   name         dob
0           0     1       RATAN NAVAL TATA  28/12/1937
1           1     2  RAMADORAI SUBRAMANIAN  06/10/1944
2           2   555    YUDHVIR SINGH MALIK  19/03/1959
3           3  1016            AJAY BHAGAT  06/08/1971
4           4  1033   RAMANATHAN NARAYANAN  14/06/1954

In [10]:
dobBOD['din'] = dobBOD['din'].apply(lambda x: str.zfill(str(x),8))

In [11]:
core1_dob = core1people.merge(dobBOD, on='din', how='inner')

In [12]:
core1_dob.head()

din                  name_x  Unnamed: 0                  name_y  \
0  00000001        RATAN NAVAL TATA           0        RATAN NAVAL TATA   
1  00000002   RAMADORAI SUBRAMANIAN           1   RAMADORAI SUBRAMANIAN   
2  00001033    RAMANATHAN NARAYANAN           4    RAMANATHAN NARAYANAN   
3  00001049          RAJESH CHHARIA           5          RAJESH CHHARIA   
4  00001050  AMIT AMARNATH BHARGAVA           6  AMIT AMARNATH BHARGAVA   

          dob  
0  28/12/1937  
1  06/10/1944  
2  14/06/1954  
3  05/03/1959  
4  22/10/1967

In [13]:
core1_dob = core1_dob.drop(columns=['Unnamed: 0', 'name_x'], axis=1)

In [14]:
core1_dob.columns

Index(['din', 'name_y', 'dob'], dtype='object')

In [15]:
core1_dob.columns = ['din', 'name', 'dob']

In [16]:
print(core1people.shape, dobBOD.shape, core1_dob.shape)

(100918, 2) (151915, 4) (80965, 3)


In [17]:
graph = Graph()

In [18]:
# get IAS details
getIASQuery = 'match (x:iasofficer) return x.name as name, x.dob as dob, x.uuid as uuid, x.iasid as iasid'
result = graph.data(getIASQuery)

In [19]:
iasDf = pd.DataFrame(result)

In [20]:
iasDf.head(5)

dob       iasid                      name    uuid
0    -4233600  01AM024300      KAILASH CHAND SAMRIA   45190
1   -15465600  01AM024600          Shri Niraj Verma  155153
2   -81302400  01AP811012        Shri K. Kanna Babu  155154
3  -379814400  01AM018000  Shri Kuljit Singh Kropha  155155
4  -359337600  01AM018005               Ms. T Y Das  155156

In [21]:
iasDf.columns = ['dob', 'iasid', 'name', 'ias_uuid']

In [22]:
iasDf.shape

(11531, 4)

In [23]:
iasDf['dob'] = pd.to_numeric(iasDf[iasDf['dob'] != 'NULL']['dob'])

In [24]:
def convertDOB(x):
    if not pd.isna(x):
        return datetime.strftime(datetime.fromtimestamp(x), '%d/%m/%Y') 
    return np.nan

In [25]:
iasDf['dob'] = iasDf['dob'].apply(convertDOB)

In [26]:
mergedDf = core1_dob.merge(iasDf, on='dob', how='inner')

In [27]:
mergedDf.head()

din                  name_x         dob       iasid  \
0  00000002   RAMADORAI SUBRAMANIAN  06/10/1944  01UT016813   
1  00340020  SUBHASH CHANDER CHOPRA  06/10/1944  01UT016813   
2  00001033    RAMANATHAN NARAYANAN  14/06/1954  01AM017500   
3  00001033    RAMANATHAN NARAYANAN  14/06/1954  01KN808001   
4  00791168   MADHAVAKUMAR KUZHIYIL  14/06/1954  01AM017500   

               name_y  ias_uuid  
0    Shri AK PAITANDY    166708  
1    Shri AK PAITANDY    166708  
2    Dr. B V Papa Rao    162519  
3  Shri R. Shantharaj    164471  
4    Dr. B V Papa Rao    162519

In [28]:
res = []
for i in range(mergedDf.shape[0]): 
    n = em.processName(mergedDf.iloc[i]['name_x'])
    m = em.processName(mergedDf.iloc[i]['name_y'])
    n_sl = n.replace(' ', '')
    m_sl = m.replace(' ', '')

    if n == m:
        res.append(mergedDf.iloc[i])

    elif em.compare(n, m) or em.leven(n_sl, m_sl) < 4:
        res.append(mergedDf.iloc[i])

In [29]:
print('Number of IAS officers which are BOD also = ', len(res))

Number of IAS officers which are BOD also =  982


In [30]:
iasFoundBOD = pd.DataFrame(res)

In [31]:
iasFoundBOD = iasFoundBOD.reset_index(drop=True)

In [32]:
iasFoundBOD.to_csv('iasWhichAreBOD.csv')

In [33]:
iasFoundBOD.head()

din                     name_x         dob       iasid  \
0  07030950        SITHERASENAN LINGAM  04/05/1956  01TN909002   
1  05178826   KANDATHIL MATHEW ABRAHAM  30/12/1957  01KL013900   
2  06459343         RAJESH KUMAR SINGH  01/07/1967  01UP062403   
3  06754022       PRAMOD KUMAR MEHERDA  11/11/1970  01OR027100   
4  01802220  SRIKANT HUCHCHAPPA WALGAD  01/06/1964  01HY020900   

                     name_y  ias_uuid  
0       SITHERASENAN LINGAM     79958  
1           Dr. K M Abraham    156565  
2        RAJESH KUMAR SINGH     71874  
3  Dr. Pramod Kumar Meherda    157373  
4      Shri Shrikant Walgad    156028

In [34]:
checkIfAlreadyStoredAsBod = 'match (n:iasofficer) where n.uuid = {} return labels(n) as labels'
addDinQuery = "match(n) where n.iasid = '{}' set n:businessperson, n.din='{}' return n.uuid"
alreadyExistMessage = []
label_added_count = 0
error = 0
for i in range(iasFoundBOD.shape[0]):
    try:
        res = graph.data(checkIfAlreadyStoredAsBod.format(iasFoundBOD.iloc[i]['ias_uuid']))
        if 'businessperson' in res[0].get('labels'):
            print(i, iasFoundBOD.iloc[i]['ias_uuid'], ' already has bod label')
            continue
        res = graph.data(addDinQuery.format(iasFoundBOD.iloc[i]['iasid'], iasFoundBOD.iloc[i]['din']))
        if len(res) != 1:
            print(i, 'Error')
        else:
            label_added_count += 1
    except ConstraintError as e:
        print(i, iasFoundBOD.iloc[i]['ias_uuid'], ' does not have bod label but there is another node with same din')
        alreadyExistMessage.append(e)
        error += 1
print('Labels added to ', label_added_count)
print('Error in ', error)
print('Already had businessperson label ', iasFoundBOD.shape[0]-error-label_added_count)

0 79958  already has bod label
1 156565  does not have bod label but there is another node with same din
2 71874  already has bod label
4 156028  does not have bod label but there is another node with same din
5 77116  already has bod label
6 157537  does not have bod label but there is another node with same din
7 19279  already has bod label
8 63215  already has bod label
9 33908  already has bod label
10 61665  already has bod label
11 64777  already has bod label
12 72141  already has bod label
14 37035  already has bod label
15 160903  does not have bod label but there is another node with same din
16 161207  does not have bod label but there is another node with same din
17 67623  already has bod label
19 52808  already has bod label
20 76243  already has bod label
21 157446  already has bod label
22 22369  already has bod label
23 52409  already has bod label
25 156805  does not have bod label but there is another node with same din
26 59829  already has bod label
27 161133  doe

250 164521  does not have bod label but there is another node with same din
251 156455  does not have bod label but there is another node with same din
252 155775  already has bod label
253 156551  does not have bod label but there is another node with same din
255 52583  already has bod label
256 4648  already has bod label
258 40667  already has bod label
260 164274  does not have bod label but there is another node with same din
261 8865  already has bod label
262 161492  already has bod label
263 55168  already has bod label
264 60841  already has bod label
265 19630  already has bod label
267 5027  already has bod label
268 40302  already has bod label
269 165870  does not have bod label but there is another node with same din
271 61941  already has bod label
274 47176  already has bod label
275 156662  does not have bod label but there is another node with same din
276 59694  already has bod label
277 55781  already has bod label
278 155197  does not have bod label but there is a

516 78049  already has bod label
517 54600  already has bod label
518 155616  already has bod label
519 157456  already has bod label
520 159309  does not have bod label but there is another node with same din
522 48105  already has bod label
524 15512  already has bod label
526 158373  does not have bod label but there is another node with same din
527 156386  already has bod label
528 58746  already has bod label
529 157956  does not have bod label but there is another node with same din
531 157043  does not have bod label but there is another node with same din
533 157962  does not have bod label but there is another node with same din
534 161613  does not have bod label but there is another node with same din
535 157927  does not have bod label but there is another node with same din
537 158272  does not have bod label but there is another node with same din
538 158771  already has bod label
539 45997  already has bod label
540 158162  does not have bod label but there is another n

775 82291  already has bod label
776 77926  already has bod label
777 27725  already has bod label
778 57862  already has bod label
780 53256  already has bod label
781 65619  already has bod label
782 25098  already has bod label
784 59419  already has bod label
785 155371  already has bod label
786 72204  already has bod label
787 25822  already has bod label
789 48637  already has bod label
790 80313  already has bod label
791 155891  already has bod label
792 42608  already has bod label
793 45645  already has bod label
794 160912  does not have bod label but there is another node with same din
795 26326  already has bod label
796 57242  already has bod label
797 36810  already has bod label
799 58947  already has bod label
800 164614  already has bod label
801 33127  already has bod label
802 51147  already has bod label
803 68212  already has bod label
806 158757  does not have bod label but there is another node with same din
807 162197  does not have bod label but there is anot

In [35]:
print('Already present as BOD', len(alreadyExistMessage))

Already present as BOD 154


In [36]:
with open('AlreadyExistingDINS.txt', 'w') as fil:
    for errorMessage in list(map(str,alreadyExistMessage)):
        print(errorMessage, file=fil)

In [37]:
maxUUIDQuery = 'match (n) return max(n.uuid) as maxUUID'
res = graph.data(maxUUIDQuery)
maxUUID = res[0]['maxUUID']
print(maxUUID)

238115


In [38]:
uuid = maxUUID +1
checkBusinessPerson = 'match (n:businessperson) where n.din = "{}" return n'
createBusinessPerson = 'create (n:businessperson:entity:person:indian {{uuid:{}, name:"{}", din:"{}"}}) return n'
for i in range(core1people.shape[0]):
    din = str.zfill(core1people.iloc[i]['din'],8)
    name = core1people.iloc[i]['name']
    result = graph.data(checkBusinessPerson.format(din))
    if len(result) == 0:
        uuid += 1
        result = graph.data(createBusinessPerson.format(uuid, name, din))
        if len(result) == 0:
            print('Can not insert {} with din {}'.format(name, din))
    else:
        print('Already exist {} with din {}'.format(name, din))

Already exist RATAN NAVAL TATA with din 00000001
Already exist RAMADORAI SUBRAMANIAN with din 00000002
Already exist RAMANATHAN NARAYANAN with din 00001033
Already exist RAJESH CHHARIA with din 00001049
Already exist BALKUMAR KAPURCHAND AGARWAL with din 00001085
Already exist PRIYANKA GAUTAM MORARKA with din 00001088
Already exist PAVAN KUMAR VIJAY with din 00001110
Already exist JAGDISH PRAKASH with din 00001115
Already exist SURENDRA KUMAR SOMANY with din 00001131
Already exist SURESH KUMAR JATIA with din 00001143
Already exist GAUTAM RAMANLAL DIVAN with din 00001176
Already exist RAHUL GAUTAM DIVAN with din 00001178
Already exist ANUPAM CHAMARIA with din 00001203
Already exist ALOK CHAMARIA with din 00001205
Already exist SUBRAMANIAN PADMANABHAN with din 00001207
Already exist SANJAY ATHA with din 00001208
Already exist VIPIN SEHGAL with din 00001214
Already exist PRITHVI PAL SINGH HALDEA with din 00001220
Already exist PRIYANKA HALDEA with din 00001221
Already exist ATUL TANTIA wit

Already exist PANKAJ JAYAKUMAR GANDHI with din 00001858
Already exist NAVIN CHANDRAKANT CHOKSHI with din 00001867
Already exist KUNTAL HASMUKHLAL SHAH with din 00001868
Already exist MADHVI AHUJA with din 00001869
Already exist PREETHA REDDY with din 00001871
Already exist SUNEETA REDDY with din 00001873
Already exist SANGEETA BHUSHAN with din 00001874
Already exist NISHA AHUJA with din 00001875
Already exist SANT KUMARI AGGARWAL with din 00001877
Already exist YOGENDRA PREMKRISHNA TRIVEDI with din 00001879
Already exist ASHWIN CHANDRAN with din 00001884
Already exist SARATHCHANDRAN DAMOTHARAN with din 00001885
Already exist RAMKRISHNA ANANTHNARAYAN with din 00001886
Already exist JAGANATH THULASIDHARAN with din 00001893
Already exist MEERAMOHIDEEN SHAIK SULTAN with din 00001896
Already exist VENKATESWARAN KRISHNASWAMY with din 00001899
Already exist DEVARAJAN SAMBANDAM with din 00001910
Already exist DINESH JAIN with din 00001912
Already exist SUBBIAH KARTHIKEYAN with din 00001922
Alr

Already exist DEBOPAMA SEN with din 00002611
Already exist RANJITSINH ABHAYSINH PARMAR with din 00002613
Already exist SANJAY OMPRAKASH NAYAR with din 00002615
Already exist AMIRALI ESSABHAI RAYANI with din 00002616
Already exist JAI SHAH with din 00002622
Already exist PRAKASH KACHOLIA with din 00002626
Already exist AJAY RELAN with din 00002632
Already exist VIJAY RAMCHANDRA MUKHI with din 00002633
Already exist KAVAS DARA PATEL with din 00002634
Already exist RUPAL PANKAJ SARAIYA with din 00002641
Already exist VENKATASAMY JAGANNATHAN with din 00002643
Already exist SANDEEP AGGARWAL with din 00002646
Already exist RAGHAVAN SADAGOPAN with din 00002647
Already exist AMIN AMIRALI RAYANI with din 00002652
Already exist RUDRAPPANAIDU SRINIVASAN with din 00002653
Already exist PANKAJ PRATAPSINH SARAIYA with din 00002659
Already exist RANGARAJAN GOPALAN with din 00002666
Already exist RAJNEESH OSWAL with din 00002668
Already exist ANIL MAHADEO NAIK with din 00002670
Already exist VINOD KUM

Already exist PAWAN KUMAR AGRAWAL with din 00003325
Already exist SANGAMPALAYAM VEDANAYAGAM BALAKRISHNAN with din 00003330
Already exist RAMESH MEHRA with din 00003334
Already exist ASHOK KHANNA with din 00003335
Already exist SURENDRA SINGH with din 00003337
Already exist CHANDRASEKHARAN BHASKAR with din 00003343
Already exist AJAYKUMAR BASANTILAL MALPANI with din 00003345
Already exist JANARTHANANAIDU RAGHUPATHY with din 00003351
Already exist RAGHUPATHY RAVICHANDRAN with din 00003352
Already exist RAGHUPATHY VASANTHKUMAR with din 00003355
Already exist JAGADEESA PANCHAMI with din 00003356
Already exist HARJEET SINGH WAHAN with din 00003358
Already exist SHIBAN KISHEN KOUL with din 00003360
Already exist ARUN DEORA with din 00003367
Already exist SUNIL KUMAR PANDEY with din 00003371
Already exist SANDEEP RAMDAS DAGA with din 00003375
Already exist P SUNDARARAJAN with din 00003380
Already exist DASARI UDAY KUMAR REDDY with din 00003382
Already exist SUNDARARAJAN LATHA with din 0000338

Already exist SUHAS GHANASHYAM KULKARNI with din 00003936
Already exist PRATEEP KUMAR GUHA with din 00003937
Already exist KEKI MANCHERSHA ELAVIA with din 00003940
Already exist HARSHBEENA SAHNEY ZAVERI with din 00003948
Already exist TUSHAR KOTHARI with din 00003949
Already exist SRIDHAR MITTA with din 00003952
Already exist DEVESH SINGH SAHNEY with din 00003956
Already exist DEEPAK KAPOOR with din 00003959
Already exist VINEET JAIN with din 00003962
Already exist RAJESH CHOPRA with din 00003964
Already exist PRIYANKA with din 00003965
Already exist PRATAP REDDY ANDE with din 00003967
Already exist RAGHAVACHARI SRINIVASAN with din 00003968
Already exist SARITA SARAF with din 00003972
Already exist UDAY SHANKARRAO PATIL with din 00003978
Already exist RAJESH KUMAR JINDAL with din 00003980
Already exist HARISH KUMAR SUREKA with din 00003987
Already exist ASHOK KUMAR AGARWAL with din 00003988
Already exist ROHITKUMAR NARAYANDASJI SARAF with din 00003994
Already exist SANJIV SARAF with di

...

Already exist POOJA NARENDRAKUMAR SANGHAVI with din BRUPS4308D
Already exist KILPA SHAH with din BRUPS5871F
Already exist MONICA SADANA with din BRWPS6294N
Already exist SWETA RAMESHKUMAR BAJAJ with din BRXPB3444G
Already exist MITALI KETAN SHAH with din BRZPS9096P
Already exist LIONEL JEAN MARIE with din BSBPG7662Q
Already exist PRANALI PURUSHOTTAM KADAM with din BSBPK3231M
Already exist VIJAY SHREENIVAS KARANAM with din BSCPK7151D
Already exist AMIT BANKATLALJI MUNDADA with din BSDPM3714P
Already exist CHANDRAKANT SHARMA with din BSDPS2436J
Already exist FORUM SURYAKANT SHAH with din BSFPS3367C
Already exist LEOPOLDO ESTEFANO MAGGIOLO GONZALEZ with din BSHPG0549Q
Already exist RAVIRAJ SUBHASH SONTAKKE with din BSIPS2390N
Already exist PRIYA PANDEY with din BSJPP6706L
Already exist RAJENDRA KUMAR KAR with din BSKPK7601Q
Already exist HIRVA KISHOREBHAI SHAH with din BSLPS2665H
Already exist NAVNEET KAUR with din BSNPK7571C
Already exist PRITI MILAN SHAH with din BSNPS2898Q
Already exis

Already exist KHUSHBU MITTAL with din BZKPM6113L
Already exist SWATI SHARMA with din BZLPS9178J
Already exist PRABAL BORDIYA with din BZNPB0766P
Already exist R. ADITYA SUBRAMANYAM with din BZNPS6534A
Already exist RAVI KUMAR SULUVA with din BZNPS7928A
Already exist PALLAVI KHURANA with din BZOPK6514P
Already exist MATTE KOTI BHASKARA TEJA with din BZOPM5061M
Already exist MADHURI GULGULIA with din BZPPB7850L
Already exist SHIFALI SITARAM SUVARNA with din BZPPS2686P
Already exist RITU DAMANI with din BZQPD5057G
Already exist SIVARAM with din BZRPS6811G
Already exist ANIL KUMAR SOOD with din BZTPS8369H
Already exist NEHA PANSARI with din BZUPK0444A
Already exist PUJA SHUKLA with din BZUPS2583Q
Already exist KULDEEP MISHRA with din BZWPM9306D
Already exist SHILPA ANIL BHARGAVA with din BZYPB0702N
Already exist MANPREET KAUR SAINI with din BZYPK3326F
Already exist RASMIRANJAN PARIDA with din BZZPP6850J
Already exist ATUL KUMAR with din CAAPK5146F
Already exist PRIYANKA PATHAK with din CAC

Already exist KRISHNA KUMAR with din CIFPK6083E
Already exist Priyanshu Kumar Kandhway with din CIFPK7183M
Already exist MADHU BALA SHARMA with din CIIPS9700D
Already exist PUNAM SINGH with din CIIPS9973C
Already exist Bhavik Kantilal Sudra with din CIKPS0230G
Already exist SUBRATA DUTTA with din CILPD5332B
Already exist Gyaneshwar Kameshwar Singh with din CILPS0936G
Already exist MAMTA NEERAJ SAHAL with din CILPS1365M
Already exist SINI PG with din CIMPS0692C
Already exist PRIYANKA SENGAR with din CINPS1814F
Already exist SHARATKUMAR KUTTY SHETTY with din CINPS5077A
Already exist VILAKSHNA PANDIT with din CIPPP0705G
Already exist DEEPAK KUMAR SHARMA with din CIPPS7591K
Already exist SHREYANS LODHA with din CISPS2517N
Already exist ADNAN SHABBIRAHMED SHAIKH with din CITPS5483A
Already exist SIDDHARTH SARRAF with din CIUPS4082E
Already exist BRIJESH KUMAR PANDEY with din CIXPP7177E
Already exist PURVESH UMESH PANDIT with din CIYPP6393P
Already exist SAGAR BHANUDAS SAKORKAR with din CJEP

Already exist HARSHANK GAUTAMKUMAR SHAH with din DABPS5341Q
Already exist NAMRATA SAJNANI with din DAFPS6449F
Already exist Enrico Malerba with din DAHPM3642A
Already exist VANDANA SINGH with din DAJPS0568H
Already exist RAMAN KANT SHARMA with din DAOPS0426P
Already exist SURBHI SHAH with din DAPPS9615M
Already exist VAIBHAVI VIJAY KUMAR SHAH with din DASPS7849G
Already exist APARNA RAJARAM SHINDE with din DASPS9793H
Already exist MONIKA MUKESHKUMAR SHAH with din DAUPS6590A
Already exist SMRITI SUHASARIA with din DAUPS7429Q
Already exist B.S VIJAY KUMAR with din DAXPK9214C
Already exist RENU KUMARI with din DBDPK3639A
Already exist SWAGAT SIBBAL with din DBJPS5167R
Already exist SUNIL KUMAR with din DBKPK1659F
Already exist GARIMA PRIYANI with din DBLPP0466G
Already exist SHANU PATANIA with din DBPPS1518J
Already exist AKHIL SHARMA with din DBZPS3260R
Already exist SURBHI SATI with din DCFPS4999A
Already exist TANNU SHARMA with din DCJPS1228E
Already exist JITENDER SHARMA with din DCJP

Already exist JAYAPAL SACHITHANANTHAN with din FASPS0644P
Already exist STUTI SINHA with din FASPS2997K
Already exist SANGEETHA CHINNASAMY with din FBHPS7970C
Already exist RAGHAV SHARMA with din FBWPS7118P
Already exist VANDANA SHARMA with din FDFPS0505D
Already exist SUGUNA M. with din FDFPS5638F
Already exist KHUSHBU GIRISH KUMAR SHAH with din FDIPS4044A
Already exist POOJA RAJESHKUMAR SHAH with din FDKPS8413K
Already exist Sucharitra Sahoo with din FEAPS1236F
Already exist Nikita Sureka with din FEMPS9989R
Already exist SAGAR HARSHADKUMAR SONI with din FGEPS2498B
Already exist SHIVANI SARDA with din FGKPS9094F
Already exist PRITI SINGH with din FGMPS6908C
Already exist MAMTA SHARMA with din FGQPS7039C
Already exist HITESHI RAJENDRA SHAH with din FHGPS2177N
Already exist SHUBHANGI SHUKLA with din FHUPS7781A
Already exist PRATYAKSH SHIVAM with din FJDPS4350G
Already exist SHIWANI SHARMA with din FKDPS6086L
Already exist SHRUTI VISHWANATH SHETTY with din FLIPS5001K
Already exist Shefa

In [39]:
res = graph.data(maxUUIDQuery)
maxUUIDAfterPush = res[0]['maxUUID']
print(maxUUIDAfterPush)

272029


In [40]:
maxUUIDAfterPush - maxUUID

33914

In [41]:
core1people.shape

(100918, 2)